## Text categorization with simple one-hot representation

In [2]:
import collections, codecs
import string, glob
translator = str.maketrans(string.punctuation, ' ' * len(string.punctuation))
dirs = glob.glob('20news-bydate-train/*')

import nltk
stopwords = set(nltk.corpus.stopwords.words('english'))
ps = nltk.stem.PorterStemmer()

In [ ]:
# train_set = []
# train_labels = []
# total_counts = collections.Counter()
# for directory in dirs:
#     filenames = glob.glob(directory + '/*')
#     print(directory, len(filenames))
#     for filename in filenames:
#         with codecs.open(filename, 'r', 'latin1') as f:
#             lines = f.readlines()
#             lines_proc = [ ps.stem(y) for x in lines for y in x.strip().lower().translate(translator).split()]
#             count = collections.Counter(lines_proc)
#             total_counts += count
#             train_set.append(count)
#             train_labels.append(directory)

In [ ]:
vocab_counts = { w : c for w,c in total_counts.items() if c > 9 and w not in stopwords and w[0] not in set('0123456789') }
vocab = { w : i for i,w in enumerate(sorted(vocab_counts.keys())) }

In [ ]:
vocab_array = sorted(vocab_counts.keys())

In [ ]:
len(vocab_array)

In [ ]:
from scipy.sparse import lil_matrix

In [ ]:
# X = lil_matrix((len(train_set), len(vocab)))
# for iDoc, doc in enumerate(train_set):
#     for w,c in doc.items():
#         if w in vocab:
#             X[ iDoc, vocab[w] ] = c

In [16]:
import numpy as np
import scipy as sp

In [ ]:
# labels_array = sorted(collections.Counter(train_labels).keys())
# labels_dict = { l : i for i,l in enumerate(labels_array) }
# y = np.array([ labels_dict[x] for x in train_labels ])

In [3]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

In [4]:
def my_tokenizer(s):
    return [ ps.stem(y) for y in s.strip().lower().translate(translator).split()]

In [5]:
cv = CountVectorizer(input='filename', encoding='latin1', tokenizer=my_tokenizer, stop_words=stopwords)
tfv = TfidfVectorizer(input='filename', encoding='latin1', tokenizer=my_tokenizer, stop_words=stopwords)

In [6]:
X = tfv.fit_transform([filename for directory in dirs for filename in glob.glob(directory + '/*')])

In [17]:
y_labels = [directory.split('/')[-1] for directory in dirs for filename in glob.glob(directory + '/*')]
y_label_dict = { x : i for i, x in enumerate(set(y_labels))}
y = np.array([ y_label_dict[x] for x in y_labels ])

In [18]:
y

array([14, 14, 14, ...,  1,  1,  1])

In [7]:
vocab_array = tfv.get_feature_names()

In [8]:
from sklearn.naive_bayes import BernoulliNB, MultinomialNB

In [19]:
model = MultinomialNB()
model.fit(X, y)

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [ ]:
labels_array

In [ ]:
[ (vocab_array[z[0]], z[1]) for z in sorted([ (i,x) for i,x in enumerate(model.coef_[-3]) ], key=lambda y: np.abs(y[1]), reverse=False)[:20] ]

In [ ]:
model.score(X, y)

In [ ]:
model = BernoulliNB()
model.fit(X, y)
model.score(X, y)

In [9]:
X_test = tfv.transform([filename for directory in glob.glob('20news-bydate-test/*') for filename in glob.glob(directory + '/*')])

In [20]:
y_test = np.array([ y_label_dict[x] for x in [directory.split('/')[-1] for directory in glob.glob('20news-bydate-test/*') for filename in glob.glob(directory + '/*')] ])

In [21]:
y_test

array([14, 14, 14, ...,  1,  1,  1])

In [22]:
def test_model(model, name=None):
    if not name is None:
        print(name)
    model.fit(X, y)
    print("Train set: %.5f\tTest set: %.5f" % (model.score(X, y), model.score(X_test, y_test)) )

In [23]:
test_model(MultinomialNB(), 'MultinomialNB')
test_model(BernoulliNB(), 'BernoulliNB')

MultinomialNB
Train set: 0.94308	Test set: 0.80775
BernoulliNB
Train set: 0.80714	Test set: 0.65919
